# Activité Basthon — Du GeoJSON à une carte interactive (Folium)

## Objectifs
- Comprendre la structure d’un **GeoJSON** (dictionnaire Python).
- Modifier des **propriétés** (attributs) et le **style** (couleur, opacité…).
- Générer une **carte interactive** avec **Folium**.

## Rappel indispensable
- En **GeoJSON**, les coordonnées sont dans l’ordre : **[longitude, latitude]**.
- Dans **Folium**, la plupart des appels utilisent **[latitude, longitude]** pour centrer une carte.

---

## Consignes générales
1. Exécute **chaque cellule** dans l’ordre.
2. Lis les questions et réponds **directement dans le notebook** (en Markdown) sous les cellules indiquées.
3. Quand une consigne demande de modifier du code, ne recopie pas tout : **modifie seulement ce qui est nécessaire**.
4. Sauvegarde ton travail (menu du notebook) avec ton **Nom_Prénom_Classe**.


## 1) Importer les modules

### Consigne
Exécute la cellule suivante.  
Si une erreur apparaît, lis-la et identifie le module manquant.

### Explication
- `json` sert à manipuler des données de type JSON/GeoJSON.
- `folium` sert à créer des cartes interactives.


In [ ]:
import json
import folium
from IPython.display import display

## 2) Charger un GeoJSON (exemple intégré)

### Consigne
Exécute la cellule : on crée un GeoJSON minimal contenant **1 polygone**.

### Explication
Un GeoJSON contient souvent :
- un objet principal `FeatureCollection`
- une liste `features`
- chaque `feature` a :
  - `properties` : informations (nom, couleur, etc.)
  - `geometry` : forme (Point, LineString, Polygon…)


In [ ]:
geo = {
  "type": "FeatureCollection",
  "features": [
    {
      "type": "Feature",
      "properties": {
        "nom": "Zone A",
        "fill": "#c72626",
        "fill-opacity": 0.5,
        "stroke": "#2a29c3",
        "stroke-width": 3
      },
      "geometry": {
        "type": "Polygon",
        "coordinates": [[
          [1.6130, 50.7245],
          [1.6190, 50.7245],
          [1.6190, 50.7285],
          [1.6130, 50.7285],
          [1.6130, 50.7245]
        ]]
      }
    }
  ]
}

print("Type Python :", type(geo))
print("Clés :", geo.keys())
print("Nb de features :", len(geo['features']))

## 3) Lire des informations dans le GeoJSON

### Consigne
Exécute la cellule puis réponds aux questions dans la cellule Markdown suivante.


In [ ]:
feature0 = geo["features"][0]

print("Nom :", feature0["properties"]["nom"])
print("Type de géométrie :", feature0["geometry"]["type"])
print("1er point (Lon,Lat) :", feature0["geometry"]["coordinates"][0][0])

### Questions (à répondre ici)
1. Dans ce GeoJSON, où sont stockées les **propriétés** (ex : nom, couleurs) ?  
2. Où sont stockées les **coordonnées** ?  
3. Les coordonnées du GeoJSON sont dans quel ordre ? **[Lat, Lon]** ou **[Lon, Lat]** ?  
4. Quel est le **type** de géométrie utilisé ici (Point / LineString / Polygon) ?  


## 4) Modifier les propriétés (style + attributs)

### Consigne
1. Change la couleur de remplissage (`fill`) en **vert**.
2. Change l’opacité (`fill-opacity`) à **0.35**.
3. Ajoute deux nouveaux attributs :
   - `Lieu` = "Mon établissement"
   - `Batiment` = "A"

### Astuce
Tu modifies directement le dictionnaire : `feature0["properties"]["..."] = ...`


In [ ]:
# À MODIFIER selon la consigne
feature0["properties"]["fill"] = "#00aa00"
feature0["properties"]["fill-opacity"] = 0.35

feature0["properties"]["Lieu"] = "Mon établissement"
feature0["properties"]["Batiment"] = "A"

print(feature0["properties"])

## 5) Afficher le GeoJSON sur une carte Folium

### Consigne
1. Exécute la cellule.
2. Vérifie que la carte s’affiche et que le **survol** (tooltip) montre `nom`, `Lieu`, `Batiment`.

### Explication
- On définit une fonction `style_fct` pour transformer les `properties` en style Folium.
- Attention : `folium.Map(location=[lat, lon])` utilise **[latitude, longitude]**.


In [ ]:
# Centre de la carte (Folium attend [lat, lon])
centre_lat, centre_lon = 50.7265, 1.6160

m = folium.Map(location=[centre_lat, centre_lon], zoom_start=15)

def style_fct(feat):
    p = feat["properties"]
    return {
        "color": p.get("stroke", "#000000"),
        "weight": p.get("stroke-width", 2),
        "fillColor": p.get("fill", "#ff0000"),
        "fillOpacity": p.get("fill-opacity", 0.4),
    }

folium.GeoJson(
    geo,
    style_function=style_fct,
    tooltip=folium.GeoJsonTooltip(fields=["nom", "Lieu", "Batiment"])
).add_to(m)

m

## 6) Défi : Ajouter une deuxième zone (Zone B)

### Consigne
1. Duplique la feature (Zone A) pour créer **Zone B**.
2. Renomme-la `"Zone B"`.
3. Mets une couleur orange `#ff8800`.
4. Décale la zone B en longitude de **+0.006** (pour qu’elle soit à côté).

### Indice
On peut utiliser `copy.deepcopy()` pour copier sans modifier l’original.


In [ ]:
import copy

zone_b = copy.deepcopy(geo["features"][0])
zone_b["properties"]["nom"] = "Zone B"
zone_b["properties"]["fill"] = "#ff8800"

# Décalage en longitude : +0.006
coords = zone_b["geometry"]["coordinates"][0]
zone_b["geometry"]["coordinates"][0] = [[lon + 0.006, lat] for lon, lat in coords]

geo["features"].append(zone_b)

m2 = folium.Map(location=[centre_lat, centre_lon], zoom_start=14)

folium.GeoJson(
    geo,
    style_function=style_fct,
    tooltip=folium.GeoJsonTooltip(fields=["nom"])
).add_to(m2)

m2

## 7) Exploitation / Questions finales

Réponds ci-dessous (en Markdown) :
1. Donne **2 différences** entre `properties` et `geometry` dans un GeoJSON.
2. Explique pourquoi une confusion **[lon, lat]** / **[lat, lon]** peut placer une zone **au mauvais endroit**.
3. Dans le code, quelle partie affiche le **tooltip** ? (copie la ligne correspondante)
4. Propose une amélioration : par exemple afficher aussi `Lieu` et `Batiment` au survol de Zone B.
